# Homework 2 
# Katherine Graham
### Collaborator: Arielle

This Notebook will detail Homework 2, which involves a basic capacity expansion model formulation described in [Notebook 3](https://github.com/east-winds/power-systems-optimization/tree/master/Notebooks)

First, load (or install if necessary) a set of packages you'll need for this assignment...

In [277]:
# Uncomment and run this first line if you need to install or update packages
#import Pkg; Pkg.add("JuMP"); Pkg.add("HiGHS"); Pkg.add("DataFrames"); Pkg.add("CSV")
using JuMP
using HiGHS
using DataFrames
using CSV

using Plots; plotly()
using Statistics
ENV["COLUMNS"]=120 # Set so all columns of DataFrames and Matrices are displayed

120

### Question 1 - Build the basic thermal generation expansion model

Using the example model in [Notebook 3](https://github.com/east-winds/power-systems-optimization/tree/master/Notebooks) as your guide, input the code to create a basic thermal generator capacity expansion model, including [downloading the data for Notebook 3 here](https://github.com/east-winds/power-systems-optimization/tree/master/Notebooks/expansion_data) and loading the appropriate csv files.

In [278]:
# Load the data: cost parameters for the generators
# KATQ: I downloaded the data into my working directory, but is there a way for this to just get the data from outside of the working directory ? Making the file path: "/Users/katherine/ENE_539/pso/power-systems-optimization/Notebooks/expansion_data" did not work. So i will just copy that into my hw3 data directory 
generators = DataFrame(CSV.File("hw3_data/expansion_data/generators_for_expansion.csv"))


6×13 DataFrame
 Row │ G        Description         Capex    FixedOM  VarOM  HeatRate  FuelCost  WACC     AssetLife  CRF      Annuity  ⋯
     │ String7  String31            Int64    Int64    Int64  Float64   Int64     Float64  Int64      Float64  Int64    ⋯
─────┼──────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   1 │ Geo      Geothermal          7500000   130000      0      28.4         0    0.04          30   0.0578   433500  ⋯
   2 │ Coal     Supercritical Coal  2600000   120000      8       8.1         2    0.04          30   0.0578   150280
   3 │ CCGT     Natural gas CCGT    1000000    28000      2       6.4         4    0.035         30   0.0544    54400
   4 │ CT       Natural gas CT       770000    21000      5       9.7         4    0.035         30   0.0544    41888
   5 │ Wind     Onshore wind        1000000    40000      0       1.0         0    0.03          30   0.051     51000  ⋯
   6 │ Solar    Tracking solar PV    750000    15000      0       1.0         0    0.025         30   0.0478    35850
                                                                                                       2 columns omitted

In [279]:
# Load the data: demand
demand = DataFrame(CSV.File("hw3_data/expansion_data/demand_for_expansion.csv"))

8760×2 DataFrame
  Row │ Hour   Demand 
      │ Int64  Int64  
──────┼───────────────
    1 │     1    2274
    2 │     2    2581
    3 │     3    2576
    4 │     4    2482
    5 │     5    2396
    6 │     6    2193
    7 │     7    1929
    8 │     8    1715
    9 │     9    1555
   10 │    10    1473
   11 │    11    1463
  ⋮   │   ⋮      ⋮
 8751 │  8751    2409
 8752 │  8752    2527
 8753 │  8753    2616
 8754 │  8754    2707
 8755 │  8755    2677
 8756 │  8756    2708
 8757 │  8757    2646
 8758 │  8758    2538
 8759 │  8759    2195
 8760 │  8760    2200
     8739 rows omitted

In [280]:
# Define scalar parameters
NSECost = 9000;

# Define the sets 
# Set of generators, created from the cols of generators DataFrame
G = generators.G[1:(size(generators,1)-2)];  # note we truncate wind and solar for now
H = demand.Hour;

In [281]:
# CODE TO MAKE SURE I UNDERSTAND THAT DF's INDEX STARTING AT 1
# ara = DataFrame(A = ["asdf", "1", "3"])
# print(ara.A[1])

In [282]:
# Define the model, specify the solver
Expansion_Model = Model(HiGHS.Optimizer) # using the HiGHS open source solver

# Define variables, include their nonnegativity constraints
@variables(Expansion_Model, begin
        CAP[g in G] >=0          # Generating capacity built (MW)
        GEN[g in G, h in H] >= 0 # Generation in each hour (MWh)
        NSE[h in H] >= 0         # Non-served energy in each hour (MWh)
end)

# Define constraints
@constraints(Expansion_Model, begin
    cDemandBalance[h in H], sum(GEN[g,h] for g in G) + NSE[h] == demand.Demand[h]
    cCapacity[g in G, h in H], GEN[g,h] <= CAP[g]
end)


# Define the objective function
# Note: the objective is now too long to print. It is therefore doubly important to check your code.
# minimize the total cost of all fixed costs for and total variable costs over all hours over all generators and the sum of all costs of unserved energy for all the amoutn of demand unserved over all hours
# KATNOTE: FixedCost and VarCost are both columns of the generators df. 
@objective(Expansion_Model, Min,
    sum(generators[generators.G.==g,:FixedCost][1]*CAP[g] + 
        sum(generators[generators.G.==g,:VarCost][1]*GEN[g,h] for h in H)
    for g in G) + 
    sum(NSECost*NSE[h] for h in H)
);


In [283]:
# CODE TO UNDERSTAND THE INDEXING IN THE ABOVE OBJ function
# KATNOTE: We index into a df by doing df[row,]

# THESE LINES OF CODE GET ERRORS: 
# generators[generators.G.=="Geo",FixedCost]
# generators["Geo","FixedCost"]
#  generators[Geo,"FixedCost"]
# generators[G=="Geo","FixedCost"]
# generators[:Geo,:FixedCost][1] # This one bugs me , why doesnt this work with teh rwos ? seems like it assumes evyerhting is a column or something 


# THESE LINES OF CODE GET THE SAME THING. NOTE THAT THE [1] IS AT THE END SINCE THE OUTPUT IS USUALLY A 1-D VECTOR.
# generators[generators.G.=="Geo","FixedCost"][1]
# generators[generators.G.=="Geo",:FixedCost][1]

In [284]:
# Expansion_Model
# print(G[1])
# print(value.(GEN)[G[1],:].data) # PRINTS OUT OVER ALL 8790(?) hours

# # NO ERRORS
# # print(value.(GEN)[G[1],:].data[3])
# print(value.(GEN)["Geo",:].data[3])
# print(value.(GEN)["Geo",:].data[3])
# # KATQ : WHY IS IT value.(jump variable).data


# GETS ERRORS
# print(value.(GEN)[Geo,:].data[3])

In [285]:
optimize!(Expansion_Model)

Presolving model
43800 rows, 43804 cols, 113880 nonzeros
43800 rows, 43804 cols, 113880 nonzeros
Presolve : Reductions: rows 43800(-0); columns 43804(-0); elements 113880(-0)
Solving the presolved LP
Using EKK dual simplex solver - serial
  Iteration        Objective     Infeasibilities num(sum)
          0     0.0000000000e+00 Pr: 8760(2.25679e+07) 0s
      27493     9.9087397880e+08 Pr: 0(0) 0s
Solving the original LP from the solution after postsolve
Model   status      : Optimal
Simplex   iterations: 27493
Objective value     :  9.9087397880e+08
HiGHS run time      :          0.65


In [286]:
# Record generation capacity and energy results
# KATNOTES : 
# GEN[g in G,h in H] is a variable in the model for MWh in each hour for each plant 
# NSE[h in H] is nse per hour
# CAP[g] is cap built (MW) per generator
generation = zeros(size(G,1))
for i in 1:size(G,1) 
    generation[i] = sum(value.(GEN)[G[i],:].data) # total generation for each generator over the year
end
MWh_share = generation./sum(demand.Demand).*100
cap_share = value.(CAP).data./maximum(demand.Demand).*100
results = DataFrame(
    Resource = G, 
    MW = value.(CAP).data,
    Percent_MW = cap_share,
    GWh = generation/1000,
    Percent_GWh = MWh_share
)
# Calculate how much non-served energy there was and add to results
  # The maximum MW of non-served energy is the difference 
  # between peak demand and total installed generation capacity
NSE_MW = maximum(value.(NSE).data) 
  # The total MWh of non-served energy is the difference between
  # total demand and total generation
NSE_MWh = sum(value.(NSE).data)
  # Add or "push" a new row of data to the end of the results DataFrame
push!(results, ["NSE" NSE_MW NSE_MW/maximum(demand.Demand)*100 NSE_MWh/1000 NSE_MWh/sum(demand.Demand)*100])

5×5 DataFrame
 Row │ Resource  MW       Percent_MW  GWh        Percent_GWh 
     │ String7   Float64  Float64     Float64    Float64     
─────┼───────────────────────────────────────────────────────
   1 │ Geo           0.0     0.0          0.0     0.0
   2 │ Coal          0.0     0.0          0.0     0.0
   3 │ CCGT       3328.0    69.1461   22139.4    98.1011
   4 │ CT         1290.0    26.8024     427.894   1.89603
   5 │ NSE         195.0     4.05153      0.637   0.00282259

In [287]:
# size(G)
# G
# size(G,1)
# # G[1]
# no errors
# print(sum(value.(GEN)["Geo",:].data))


# print(sum(value.(NSE)["Geo",:].data))

## Question 2: Analytical solution

**A.** Using the data provided above, sort the demand data from highest to lowest hours to create a load duration curve and save this as a vector/array/DataFrame of your choice.

In [288]:
sortD = sort(demand.Demand, rev=true) # sorts demand from highest to lowest and saves it in a vector. 
# KATQ : What's the difference between sort() and sort!() # --> Variant of sort! that returns a sorted copy of v leaving v itself unmodified.

8760-element Vector{Int64}:
 4813
 4784
 4745
 4677
 4670
 4645
 4629
 4618
 4555
 4514
 4498
 4496
 4496
    ⋮
 1356
 1350
 1349
 1344
 1344
 1337
 1337
 1333
 1326
 1321
 1319
 1306

**B.** Now using the cost data provided in '/generators_for_expansion.csv' and the load duration curve above, use the formulas provided in Lecture to determine an analytical solution to the optimal thermal generation expansion decisions (e.g. solve it algebraically rather than use an optimization solver to find the solution). 

Report the optimal capacity of each generation source and compare to the solution from the optimization model above. 

Show your work in cells below, using Julia to perform calculations. Explain your steps using inline code comments (e.g. `# Comment`) or by interspersing Markdown cells.  

Tip: round your solutions for the crossover hour between each technology to the nearest integer (as we have discrete hours in the time series).

In [289]:
generators

6×13 DataFrame
 Row │ G        Description         Capex    FixedOM  VarOM  HeatRate  FuelCost  WACC     AssetLife  CRF      Annuity  ⋯
     │ String7  String31            Int64    Int64    Int64  Float64   Int64     Float64  Int64      Float64  Int64    ⋯
─────┼──────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   1 │ Geo      Geothermal          7500000   130000      0      28.4         0    0.04          30   0.0578   433500  ⋯
   2 │ Coal     Supercritical Coal  2600000   120000      8       8.1         2    0.04          30   0.0578   150280
   3 │ CCGT     Natural gas CCGT    1000000    28000      2       6.4         4    0.035         30   0.0544    54400
   4 │ CT       Natural gas CT       770000    21000      5       9.7         4    0.035         30   0.0544    41888
   5 │ Wind     Onshore wind        1000000    40000      0       1.0         0    0.03          30   0.051     51000  ⋯
   6 │ Solar    Tracking solar PV    750000    15000      0       1.0         0    0.025         30   0.0478    35850
                                                                                                       2 columns omitted

In [290]:
# import Pkg
# Pkg.add("ImplicitEquations")

In [291]:
using ImplicitEquations

In [292]:
# First plot all the linear equations so we can know which resources are optimal at what hours
Fgeo = generators[generators.G.=="Geo","FixedCost"][1]
Fcoal = generators[generators.G.=="Coal","FixedCost"][1]
Fccgt = generators[generators.G.=="CCGT","FixedCost"][1]
Fct = generators[generators.G.=="CT","FixedCost"][1]

Vgeo = generators[generators.G.=="Geo","VarCost"][1]
Vcoal = generators[generators.G.=="Coal","VarCost"][1]
Vccgt = generators[generators.G.=="CCGT","VarCost"][1]
Vct = generators[generators.G.=="CT",:VarCost][1]

fngeo(x) = Fgeo + Vgeo*x
fncoal(x) = Fcoal + Vcoal*x
fnccgt(x) = Fccgt + Vccgt*x
fnct(x) = Fct + Vct*x
fnse(x) = 9000*x

t = 0:8760
p = plot(t, fngeo)
plot!(p, t, fncoal)
plot!(p, t, fnccgt)
plot!(p, t, fnct)
plot!(p, 0:100, fnse)

# hours = 8760
# p = plot(x, fngeo,0,hours)
# plot!(fncoal, 0, hours)
# plot!(fnccgt, 0, hours)

In [293]:
# From the graph above, the intersections in question are: 
# between the purple (Cost of CT) and green (Cost of CCGT) 
# --> set fnct and fnccgt equal to each other and solve for x
# Between the purple (Cost of CT) and yellow (Cost of unserved energy) 
# --> fnct and fnse equal to each other and solve for x

# Fct + Vct*x = Fccgt + Vccgt*x --> (Vct - Vccgt)x = Fccgt - Fct --> x = (Fccgt-Fct)/(Vct - Vccgt)
h1 = round(Int, (Fccgt-Fct)/(Vct - Vccgt))
# Fct + Vct*x = 9000*x --> (Vct - 9000)x = - Fct --> x = (-Fct)/(Vct - 9000)
h2 = round(Int, (-Fct)/(Vct - 9000))
println("h1: ", h1)
println("h2: ", h2)

# Now, determine the MW of demand at those hours. 
# --> CCGT will build the MW of demand at h1 (since every hour after that is lower than h1) 
# --> CT will build the MW of demand at h2 (since every hour after that is lower than demand at that hour)
# --> The amount of "MW" of NSE built will be the demand at hour zero. 

# Additionally, the cumulative MWh generated by each of these will be determined byyyyyyy actually we dont have to do this so nvm

println("Capacity of CCGT: ", sortD[h1])
println("Capacity of CT: ", sortD[h2+1]-sortD[h1]) # THISSSS gets the right number. kind of makes sense to offset by 1 but tbh im still confused as to why we are only offsetting one of the hours by 1
println("Capacity of NSE: ", sortD[1] - sortD[h2 + 1])
println("These are the same solutions as the capacity model ran above. Note that Geo and Coal both did not build anything because their costs never got low enough")

# IGNORE THE REST OF THESE COMMENTS ---------------------------------------
# # WITHOUT SHIFTING:
# println("Capacity of CCGT: ", sortD[h1])
# println("Capacity of CT: ", sortD[h2]-sortD[h1]) # WHY IS THIS NUMBER WRONG ??? # THISSSS gets the right number
# println("Capacity of NSE: ", sortD[1] - sortD[h2])
# # print(sortD[0])
# #CUTS: 
# # println("Capacity of CT: ", sortD[h2 + 1]-sortD[h1 - 1]) # WHY IS THIS NUMBER WRONG ???
# # println("Capacity of CT: ", sortD[h2]-sortD[h1 - 1]) # WHY IS THIS NUMBER WRONG ???

# println()
# println( sortD[h2])
# println(sortD[h1])

# println()
# println("Fccgt: ", Fccgt)
# println("Fct: ", Fct)
# println("Vccgt: ", Vccgt)
# println("Vct: ", Vct)


h1: 1204
h2: 7
Capacity of CCGT: 3328
Capacity of CT: 1290
Capacity of NSE: 195
These are the same solutions as the capacity model ran above. Note that Geo and Coal both did not build anything because their costs never got low enough


**C.** Now change the fuel cost of natural gas to \$8.00/MMBtu, recalculate the variable cost of CCGTs and CTs, and solve again for the optimal generation capacity mix. Describe what changes in your capacity results and what doesn't, and provide an explanation.

In [294]:
# First plot all the linear equations so we can know which resources are optimal at what hours
Fgeo = generators[generators.G.=="Geo","FixedCost"][1]
Fcoal = generators[generators.G.=="Coal","FixedCost"][1]
Fccgt = generators[generators.G.=="CCGT","FixedCost"][1]
Fct = generators[generators.G.=="CT","FixedCost"][1]

# Fuel cost for ng is now 
Vgeo = generators[generators.G.=="Geo","VarCost"][1]
Vcoal = generators[generators.G.=="Coal","VarCost"][1]
Vccgt = generators.VarOM[generators.G.=="CCGT",:][1] + generators.HeatRate[generators.G.=="CCGT",:][1]*8
Vct = generators.VarOM[generators.G.=="CT",:][1] + generators.HeatRate[generators.G.=="CT",:][1]*8

fngeo(x) = Fgeo + Vgeo*x # y1
fncoal(x) = Fcoal + Vcoal*x  # y2 
fnccgt(x) = Fccgt + Vccgt*x # y3
fnct(x) = Fct + Vct*x # y4
fnse(x) = 9000*x # y5

t = 0:8760
p = plot(t, fngeo)
plot!(p, t, fncoal)
plot!(p, t, fnccgt)
plot!(p, t, fnct)
plot!(p, 0:100, fnse)


In [295]:
# println("Vccgt: ", Vccgt)
# println("Vct: ", Vct)

# coal is the baseload, and takes on the demand capacity at the hour where red(coal) and green(ccgt) intersect
# Ccgt takes on the demand capacity at the hour where green(ccgt) and purple(ct) intersect minus the cap at the next hour, h1 
# CT takes on the demand cap at the hour where yellow(NSE) and purple(CT) intersect, minus the cap at the next hour, h2
# NSE takes on the demand cap at the hour 0 to the hour where yellow and purple connect 


# Fccgt + Vccgt*x = Fcoal + Vcoal*x 
h1 = round(Int,(Fcoal - Fccgt)/(Vccgt-Vcoal))

# Fccgt + Vccgt*x = Fct + Vct*x
h2 = round(Int,(Fct - Fccgt)/(Vccgt-Vct))

# Fct + Vctx = 9000*x
h3 = round(Int, (-Fct)/(Vct - 9000))

println("h1: ", h1)
println("h2: ", h2)
println("h3: ", h3)

println("Capacity of Coal: ", sortD[h1])
println("Capacity of CCGT: ", sortD[h2+1]-sortD[h1]) 
println("Capacity of CT: ", sortD[h3+1] - sortD[h2+1])
println("Capacity of NSE: ", sortD[1] - sortD[h3+1])
println("Geo is 0MW since it is not cost competitive")




h1: 6479
h2: 664
h3: 7
Capacity of Coal: 2110
Capacity of CCGT: 1471
Capacity of CT: 1037
Capacity of NSE: 195
Geo is 0MW since it is not cost competitive


When the costs of natural gas raised, the cost of coal became competitive after a certain hour, and so the capacity of coal rose and the capacity of CCGT and CT both fell, since they both relied on natural gas and their variable costs were now higher. NSE stayed the same since the coal took on all of the  capacity that CT and CC used to supply (2110 + 1471 + 1037 == 3328 + 1290). 

## Question 3 - Expansion with renewables

**A.** Using JuMP/Julia, implement an optimization model based on the formulation for optimal thermal+renewable capacity expansion provided in Section 2 of [Notebook 3](https://github.com/east-winds/power-systems-optimization/tree/master/Notebooks). 

In [296]:
generators

6×13 DataFrame
 Row │ G        Description         Capex    FixedOM  VarOM  HeatRate  FuelCost  WACC     AssetLife  CRF      Annuity  ⋯
     │ String7  String31            Int64    Int64    Int64  Float64   Int64     Float64  Int64      Float64  Int64    ⋯
─────┼──────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   1 │ Geo      Geothermal          7500000   130000      0      28.4         0    0.04          30   0.0578   433500  ⋯
   2 │ Coal     Supercritical Coal  2600000   120000      8       8.1         2    0.04          30   0.0578   150280
   3 │ CCGT     Natural gas CCGT    1000000    28000      2       6.4         4    0.035         30   0.0544    54400
   4 │ CT       Natural gas CT       770000    21000      5       9.7         4    0.035         30   0.0544    41888
   5 │ Wind     Onshore wind        1000000    40000      0       1.0         0    0.03          30   0.051     51000  ⋯
   6 │ Solar    Tracking solar PV    750000    15000      0       1.0         0    0.025         30   0.0478    35850
                                                                                                       2 columns omitted

In [297]:
variability = DataFrame(CSV.File("hw3_data/expansion_data/wind_solar_for_expansion.csv"))

8760×3 DataFrame
  Row │ Hour   Wind         Solar    
      │ Int64  Float64      Float64  
──────┼──────────────────────────────
    1 │     1  0.0296442    0.440206
    2 │     2  0.0534046    0.0
    3 │     3  0.0456225    0.0
    4 │     4  0.0908019    0.0
    5 │     5  0.177524     0.0
    6 │     6  0.196106     0.0
    7 │     7  0.163481     0.0
    8 │     8  0.129312     0.0
    9 │     9  0.131448     0.0
   10 │    10  0.162792     0.0
   11 │    11  0.169585     0.0
  ⋮   │   ⋮         ⋮          ⋮
 8751 │  8751  0.45589      0.0
 8752 │  8752  0.341911     0.115556
 8753 │  8753  0.222848     0.530593
 8754 │  8754  0.030222     0.747114
 8755 │  8755  0.0143295    0.874793
 8756 │  8756  0.0377381    0.94319
 8757 │  8757  0.0552232    0.962
 8758 │  8758  0.00819863   0.948126
 8759 │  8759  0.000661809  0.852887
 8760 │  8760  0.00255233   0.687016
                    8739 rows omitted

In [298]:
# k = 3
# j = "Wind"
# # THE NEXT THREE LINES ALL GET THE SAME RESULT. 
# variability[variability.Hour.==k,"Wind"][1]
# variability[variability.Hour.==k,:Wind][1]
# variability[variability.Hour.==k,j][1]


# THESE RESULT IN ERRORS 
# Ohhh, KATNOTE: I think it's because I wrote variability.Hour[....] and not just variability[...]
# variability.Hour[variability.Hour.==k,"Wind"][1] # KATQ: WHY IS THERE AN ERROR HERE ??? 
# variability.Hour[variability.Hour.==k,variability.Wind][1]
# variability.Hour[variability.Hour.==k,:Wind][1]




In [299]:
# Define scalar parameters
NSECost = 9000;

# Define the sets 
# Set of generators, created from the cols of generators DataFrame
# G = generators.G[1:(size(generators,1)-2)];  # note we truncate wind and solar for now
G = generators.G[:];
H = demand.Hour;
GnotRE = generators.G[1:(size(generators,1)-2)];
RE = generators.G[(size(generators,1)-1):size(generators,1)];
# for i in 1:size(RE,1)
#     print(RE[i])
# end
# for i in RE
#     println(i)
#     println(typeof(i))
# end
# println(typeof("Wind"))
# KatQ: is there an important difference between String and String7? just the size right?(?)

# Gets an error:
# RE = generators.G[generators.G.=="Wind",generators.G.=="Solar"]


In [300]:
Expansion_Model2 = Model(HiGHS.Optimizer) # using the HiGHS open source solver

@variables(Expansion_Model2, begin
        CAP[g in G] >=0          # Generating capacity built (MW)
        GEN[g in G, h in H] >= 0 # Generation in each hour (MWh)
        NSE[h in H] >= 0         # Non-served energy in each hour (MWh)
end)

@constraints(Expansion_Model2, begin
    cDemandBalance[h in H], sum(GEN[g,h] for g in G) + NSE[h] == demand.Demand[h]
    cCapacityNonRE[g in GnotRE, h in H], GEN[g,h] <= CAP[g]
    cCapacityRE[g in RE, h in H], GEN[g,h] <= CAP[g]*variability[variability.Hour.==h,g][1]
end)

# Note: the objective is now too long to print. It is therefore doubly important to check your code.
@objective(Expansion_Model2, Min,
    sum(generators[generators.G.==g,:FixedCost][1]*CAP[g] + 
        sum(generators[generators.G.==g,:VarCost][1]*GEN[g,h] for h in H)
    for g in G) + 
    sum(NSECost*NSE[h] for h in H) 
);

**B.** Solve the model to determine the optimal capacity when wind and solar are available resources and extract results for generation and capacity.

In [301]:
optimize!(Expansion_Model2)

Presolving model
56856 rows, 56862 cols, 153048 nonzeros
56856 rows, 56862 cols, 153048 nonzeros
Presolve : Reductions: rows 56856(-4464); columns 56862(-4464); elements 153048(-8928)
Solving the presolved LP
Using EKK dual simplex solver - serial
  Iteration        Objective     Infeasibilities num(sum)
          0     0.0000000000e+00 Pr: 8760(6.18517e+06) 0s
      40369     8.2899893531e+08 Pr: 0(0); Du: 0(3.19744e-13) 4s
Solving the original LP from the solution after postsolve
Model   status      : Optimal
Simplex   iterations: 40369
Objective value     :  8.2899893531e+08
HiGHS run time      :          4.06


In [302]:
# Record generation capacity and energy results
generation = zeros(size(G,1))
for i in 1:size(G,1) 
    generation[i] = sum(value.(GEN)[G[i],:].data) # total generation for each generator over the year
end
MWh_share = generation./sum(demand.Demand).*100
cap_share = value.(CAP).data./maximum(demand.Demand).*100
results = DataFrame(
    Resource = G, 
    MW = value.(CAP).data,
    Percent_MW = cap_share,
    GWh = generation/1000,
    Percent_GWh = MWh_share
)
# Calculate how much non-served energy there was and add to results
  # The maximum MW of non-served energy is the difference 
  # between peak demand and total installed generation capacity
NSE_MW = maximum(value.(NSE).data) 
  # The total MWh of non-served energy is the difference between
  # total demand and total generation
NSE_MWh = sum(value.(NSE).data)
  # Add or "push" a new row of data to the end of the results DataFrame
push!(results, ["NSE" NSE_MW NSE_MW/maximum(demand.Demand)*100 NSE_MWh/1000 NSE_MWh/sum(demand.Demand)*100])

7×5 DataFrame
 Row │ Resource  MW        Percent_MW  GWh           Percent_GWh 
     │ String7   Float64   Float64     Float64       Float64     
─────┼───────────────────────────────────────────────────────────
   1 │ Geo          0.0       0.0          0.0        0.0
   2 │ Coal         0.0       0.0          0.0        0.0
   3 │ CCGT      2422.86     50.3398   11367.7       50.3709
   4 │ CT        1419.78     29.4989     453.98       2.01162
   5 │ Wind       349.956     7.27105   1007.7        4.46518
   6 │ Solar     3362.77     69.8684    9738.16      43.1505
   7 │ NSE        136.513     2.83635      0.399328   0.00176945

**C.** What happens to the total firm generation and maximum MW of non-served energy? What does this imply about the capacity value of solar and/or wind built in the optimal capacity mix?

The total firm generation would be the CCGT and CT combined (and geo and coal are never built). The total firm generation from the first model was 3328 + 1290 = 4618MW installed capacity. In this model, the total firm generation is 2422.86 + 1419.78 = 3842.64MW. This is a decrease in installed firm capacity, which implies that the addition of Solar (3362.77MW) and Wind (349.956MW) are able to serve demand which was previously only served by firm entities. The sum of non-firm energy (Wind and solar) is 3712.726MW, which is much greater than the the decrease in installed MW of firm technologies (which equalled 4618 - 3842.64 = 775.36MW). This implies that the capacity factors for most hours of wind and solar are much lower than 1, which is the capacity factor of firm techs for all hours. It still makes economic sense though to employ so much renewables because their variable costs are nothing as compared to fuel costs of the firm resources. 

## Question 4: Brownfield Expansion Model

**A.** Now implement an optimization model based on the formulation for optimal "brownfield" thermal+renewable capacity expansion (e.g. with existing generators) provided in Section 3 of [Notebook 3](https://github.com/east-winds/power-systems-optimization/tree/master/Notebooks).

Use the following data for fixed and variable costs of existing gas capacity. Note: unlike in the formulation in Notebook 3, there is no existing renewable capacity here to consider (only thermal).

In [303]:
# Load new generator options
#path = joinpath([REPLACE THIS WITH PATH TO YOUR power-systems-optimization DIRECTORY HERE],"Notebooks","expansion_data")
# path = joinpath("/Users/jdj2/Documents/GitHub/power-systems-optimization","Notebooks","expansion_data")
path = joinpath("/Users/katherine/ENE_539/pso/power-systems-optimization"
,"Notebooks","expansion_data")

generators = DataFrame(CSV.File(joinpath(path,"generators_for_expansion.csv")))
# Add parameters for existing CCGTs, with the set index "Old"
push!(generators, ["Old_CC" "Existing CCGT" 0 40000 5 7.5 4 0 0 0 0 40000 30])
# Add parameters for existing CTs, with the set index "Old"
push!(generators, ["Old_CT" "Existing CT" 0 30000 11 11.0 4 0 0 0 0 30000 55])

# Set installed capacity for existing CCGTs:
ExistingCap_CCGT = 1260 # Approximate actual existing capacity in SDGE
ExistingCap_CT = 925 # Approximate actual existing capacity in SDGE
# Add new column to generators Data Frame
generators[!,:ExistingCap] = [0,0,0,0,0,0, ExistingCap_CCGT, ExistingCap_CT];

generators

8×14 DataFrame
 Row │ G        Description         Capex    FixedOM  VarOM  HeatRate  FuelCost  WACC     AssetLife  CRF      Annuity  ⋯
     │ String7  String31            Int64    Int64    Int64  Float64   Int64     Float64  Int64      Float64  Int64    ⋯
─────┼──────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   1 │ Geo      Geothermal          7500000   130000      0      28.4         0    0.04          30   0.0578   433500  ⋯
   2 │ Coal     Supercritical Coal  2600000   120000      8       8.1         2    0.04          30   0.0578   150280
   3 │ CCGT     Natural gas CCGT    1000000    28000      2       6.4         4    0.035         30   0.0544    54400
   4 │ CT       Natural gas CT       770000    21000      5       9.7         4    0.035         30   0.0544    41888
   5 │ Wind     Onshore wind        1000000    40000      0       1.0         0    0.03          30   0.051     51000  ⋯
   6 │ Solar    Tracking solar PV    750000    15000      0       1.0         0    0.025         30   0.0478    35850
   7 │ Old_CC   Existing CCGT             0    40000      5       7.5         4    0.0            0   0.0           0
   8 │ Old_CT   Existing CT               0    30000     11      11.0         4    0.0            0   0.0           0
                                                                                                       3 columns omitted

In [304]:
NSECost = 9000; 
G = generators.G[:];
H = demand.Hour;
Gnew = generators.G[1:(size(generators,1)-4)];
Gold = generators.G[(size(generators,1)-1):size(generators,1)];
# RE = generators.G[generators.G.=="Wind" | generators.G.=="Solar"]; # FIGURE THIS OUT LATER
RE = generators.G[5:6];
println("Gnew: ", Gnew)
println("Gold: ", Gold)
println("RE: ", RE)


# KATNOTE FOR LATER: figure out a more elegant way to make these subsets 
# (i.e. can we make a subset with just the rows that are equal to "Wind" and "Solar")

# Trying out set stuff in Julia: This would be equal to "g in NEW and RE"
println(setdiff(G, Gold))
# println(intersect(Gnew, RE)) # incorrect
println(union(Gnew, RE))

print(generators.ExistingCap[generators.G.=="Old_CC",:][1])

Gnew: String7["Geo", "Coal", "CCGT", "CT"]
Gold: String7["Old_CC", "Old_CT"]
RE: String7["Wind", "Solar"]
String7["Geo", "Coal", "CCGT", "CT", "Wind", "Solar"]
String7["Geo", "Coal", "CCGT", "CT", "Wind", "Solar"]
1260

In [305]:
Expansion_Model3 = Model(HiGHS.Optimizer) # using the HiGHS open source solver

@variables(Expansion_Model3, begin
        CAP[g in union(Gnew,RE)] >=0          # Generating capacity built (MW)
        GEN[g in G, h in H] >= 0 # Generation in each hour (MWh)
        NSE[h in H] >= 0         # Non-served energy in each hour (MWh)
        RET[g in Gold] >= 0
end);

@constraints(Expansion_Model3, begin
    cDemandBalance[h in H], sum(GEN[g,h] for g in G) + NSE[h] == demand.Demand[h]
    cCapacityGnew[g in Gnew, h in H], GEN[g,h] <= CAP[g]
    cCapacityGold[g in Gold, h in H], GEN[g,h] <= generators.ExistingCap[generators.G.==g,:][1] - RET[g]
    cCapacityREnew[g in RE, h in H], GEN[g,h] <= CAP[g]*variability[variability.Hour.==h,g][1]
end);

@objective(Expansion_Model3, Min,
    sum(generators.FixedCost[generators.G.==g,:][1]*CAP[g]
        for g in union(Gnew, RE)) + 
    sum(generators.FixedCost[generators.G.==g,:][1]*
        (generators.ExistingCap[generators.G.==g,:][1] - RET[g])
        for g in Gold) + 
    sum(sum(generators.VarCost[generators.G.==g,:][1]*GEN[g,h] for h in H)
        for g in G) + 
    sum(NSECost*NSE[h] for h in H)
);

**B.** Solve the model to determine the optimal capacity when with existing generators and extract results for generation and capacity (including retirements).

In [306]:
optimize!(Expansion_Model3)

Presolving model
74376 rows, 74384 cols, 205608 nonzeros
74376 rows, 74384 cols, 205608 nonzeros
Presolve : Reductions: rows 74376(-4464); columns 74384(-4464); elements 205608(-8928)
Solving the presolved LP
Using EKK dual simplex solver - serial
  Iteration        Objective     Infeasibilities num(sum)
          0    -6.9996449302e+04 Ph1: 17520(10432); Du: 2(69996.4) 0s
      41632     7.3785316204e+08 Pr: 12280(5.22045e+06); Du: 0(7.59295e-08) 5s
      46776     7.5494110973e+08 Pr: 0(0); Du: 0(5.50102e-11) 9s
Solving the original LP from the solution after postsolve
Model   status      : Optimal
Simplex   iterations: 46776
Objective value     :  7.5494110973e+08
HiGHS run time      :          9.68


In [307]:
# [value.(CAP).data, generators.ExistingCap[generators.G.=="Old_CC"], generators.ExistingCap[generators.G.=="Old_CT"]]
# append!(value.(CAP).data,generators.ExistingCap[generators.G.=="Old_CC"], generators.ExistingCap[generators.G.=="Old_CT"])

# value.(RET)["Old_CC"].data
# value.(RET)[1].data
# value.(RET)[1,:].data
# G[1]
# value.(RET)["Old_CC"].data # KATQ WHY DOESN'T THIS WORK ?? ESPECIALLY WHEN THE BELOW LINE WORKS ? 
# sum(value.(GEN)[G[4],:].data)
# value.(RET)[G[7]].data # SAME QUESTION ?

# # this works tho ???
# println(value.(RET).data[1])

# value.(RET).data
# # sum(value.(GEN)[G,:].data) # sums everything 


In [308]:
# Record generation capacity and energy results
generation = zeros(size(G,1))
for i in 1:size(G,1) 
    generation[i] = sum(value.(GEN)[G[i],:].data) # total generation for each generator over the year
end
MWh_share = generation./sum(demand.Demand).*100
cap_share = (append!(value.(CAP).data,generators.ExistingCap[generators.G.=="Old_CC"] .- value.(RET).data[1], generators.ExistingCap[generators.G.=="Old_CT"].- value.(RET).data[2]))/maximum(demand.Demand).*100
results = DataFrame(
    Resource = G, 
    MW = append!(value.(CAP).data,generators.ExistingCap[generators.G.=="Old_CC"] .- value.(RET).data[1], generators.ExistingCap[generators.G.=="Old_CT"].- value.(RET).data[2]),
    Percent_MW = cap_share,
    GWh = generation/1000,
    Percent_GWh = MWh_share,
    Retired_MW = append!(zeros(6),value.(RET).data[1], value.(RET).data[2])
)
# Calculate how much non-served energy there was and add to results
  # The maximum MW of non-served energy is the difference 
  # between peak demand and total installed generation capacity
NSE_MW = maximum(value.(NSE).data) 
  # The total MWh of non-served energy is the difference between
  # total demand and total generation
NSE_MWh = sum(value.(NSE).data)
  # Add or "push" a new row of data to the end of the results DataFrame
push!(results, ["NSE" NSE_MW NSE_MW/maximum(demand.Demand)*100 NSE_MWh/1000 NSE_MWh/sum(demand.Demand)*100 0])

9×6 DataFrame
 Row │ Resource  MW        Percent_MW  GWh          Percent_GWh  Retired_MW 
     │ String7   Float64   Float64     Float64      Float64      Float64    
─────┼──────────────────────────────────────────────────────────────────────
   1 │ Geo          0.0       0.0         0.0        0.0                0.0
   2 │ Coal         0.0       0.0         0.0        0.0                0.0
   3 │ CCGT      1417.31     29.4476   8545.01      37.8636             0.0
   4 │ CT         238.555     4.95648   105.948      0.469465           0.0
   5 │ Wind       385.045     8.00009  1111.73       4.92614            0.0
   6 │ Solar     3357.62     69.7615   9717.83      43.0604             0.0
   7 │ Old_CC    1260.0      26.1791   2973.4       13.1754             0.0
   8 │ Old_CT     925.0      19.2188    113.611      0.503418           0.0
   9 │ NSE        125.066     2.5985      0.366094   0.00162219         0.0